Scrape https://patents.google.com/ for images from specific publication numbers

In [1]:
import requests
from bs4 import BeautifulSoup as BS
import os
import time
import pandas as pd
import json
import re
import shutil

In [2]:
SLEEP_IMAGES = 0.25 # seconds to pause between images
SLEEP_PATENT = 0.5 # seconds to pause between patents

In [3]:
# test variables

# URL = "https://realpython.github.io/fake-jobs/"
# URL = "https://patents.google.com/patent/EP3619893B1"
# identifier = "EP3619893B1"
# URL = "https://patents.google.com/patent/US2021323767A1"
# URL = "https://patents.google.com/patent/EP3895010A1"
# URL = "https://patents.google.com/patent/US20210309346A1"
# identifier = "US-2021309346-A1"
URL = "https://patents.google.com/patent/WO2021180039A1"
identifier = "WO-2021180039-A1"

In [4]:
json_input = "json_data/keyword_search_data_20211126.json"
# json_input = "json_data/assignee_search_data_20211203.json"

In [5]:
base_url = "https://patents.google.com/patent/"
root_folder = "image_downloads"
current_download = None

print("running patent scraper")
print("*" * 20)


json_inputs = ["json_data/assignee_search_data_20211203.json",
               "json_data/keyword_search_data_20211126.json"                ]

try:
    for json_input in json_inputs:

        print(f'--- loading input: {json_input} ---')

        all_data = []
        for line in open(json_input, 'r'):
            all_data.append(json.loads(line))
        df = pd.DataFrame(all_data)
        pubs = df["publication_number"]

        total_pubs = len(pubs)

        for i, pub in enumerate(pubs[:]):
            print(f'i: {i} / {total_pubs} --- publication_number: {pub}')
            identifier = pub
            text = pub
            # clean up some of the specific publication_number formats
            text = re.sub(r'(US-2021)', r'\g<1>0', text)
            text = re.sub(r'(US-2005)', r'\g<1>0', text)
            text = re.sub(r'(US-D\d\d\d\d\d\d-S)', r'\g<1>1', text)

            # remove dashes for the URL
            formatted = text.replace("-", "")
            URL = base_url + formatted
            print(f'URL: {URL}')

            target_folder = os.path.join(root_folder, identifier)
            #     print(f'target_folder {target_folder}')

            if not os.path.exists(target_folder):
                print(f'making directory {target_folder}')
                os.mkdir(target_folder)
                current_download = target_folder

                page = requests.get(URL)
            #     print(page.text)
                soup = BS(page.content, "html.parser")

                # get all image URLs
                results = soup.find_all(itemprop="full")
                print(f'found {len(results)} images')
            #     for result in results:
            #         print(result['content'])

                pdf_results = soup.find_all(itemprop="pdfLink")
                print(f'found {len(pdf_results)} PDFs')

                # get all images    
                for result in results:
                    img_url = result['content']
                    img_name = os.path.basename(img_url)
        #             print(img_name)
                    save_file_path = os.path.join(target_folder, img_name)
        #             print(save_file_path)

                    if not os.path.exists(save_file_path):
                        print(f'downloading {img_name} to {save_file_path}')
                        img_data = requests.get(img_url).content
                        with open(save_file_path, 'wb') as handler:
                            handler.write(img_data)
                        time.sleep(SLEEP_IMAGES)
                    else:
                        print(f'file {save_file_path} already exists')

                # get PDF
                for pdf_result in pdf_results:
                    pdf_url = pdf_result['href']
                    print(pdf_url)
            #         print(pdf_result)
                    pdf_name = pdf_result['href'].rsplit("/", 1)[1]
            #         print(pdf_name)
                    pdf_save_file_path = os.path.join(target_folder, pdf_name)
            #         print(pdf_save_file_path)

                    if not os.path.exists(pdf_save_file_path):
                        print(f'downloading {pdf_name} to {pdf_save_file_path}')
                        pdf_data = requests.get(pdf_url).content
                        with open(pdf_save_file_path, 'wb') as handler:
                            handler.write(pdf_data)
                        time.sleep(SLEEP_IMAGES)
                    else:
                        print(f'PDF {pdf_save_file_path} already exists')

                current_download = None # finished download
                time.sleep(SLEEP_PATENT) # pause before next patent


            else:
                print(f'folder {target_folder} already exists, continuing to next publication_number')

            print("*" * 20)

    print("scraping complete")
except OSError as e:
    print ("Error: %s - %s." % (e.filename, e.strerror))
finally:
    if current_download:
        if os.path.isdir(current_download):
            shutil.rmtree(current_download)
            print("-" * 20)
            print("cleaning up")
            print(f'deleting current download directory {current_download}')
            print("-" * 20)
        else:
            print(f'Error: {current_download} directory does not exist')

running patent scraper
********************
--- loading input: json_data/assignee_search_data_20211203.json ---
i: 0 / 37660 --- publication_number: EP-3619893-B8
URL: https://patents.google.com/patent/EP3619893B8
folder image_downloads/EP-3619893-B8 already exists, continuing to next publication_number
********************
i: 1 / 37660 --- publication_number: EP-3786085-A4
URL: https://patents.google.com/patent/EP3786085A4
folder image_downloads/EP-3786085-A4 already exists, continuing to next publication_number
********************
i: 2 / 37660 --- publication_number: EP-3899827-A1
URL: https://patents.google.com/patent/EP3899827A1
folder image_downloads/EP-3899827-A1 already exists, continuing to next publication_number
********************
i: 3 / 37660 --- publication_number: US-2021323767-A1
URL: https://patents.google.com/patent/US20210323767A1
folder image_downloads/US-2021323767-A1 already exists, continuing to next publication_number
********************
i: 4 / 37660 --- publi

folder image_downloads/US-11080596-B1 already exists, continuing to next publication_number
********************
i: 718 / 37660 --- publication_number: US-11080041-B1
URL: https://patents.google.com/patent/US11080041B1
folder image_downloads/US-11080041-B1 already exists, continuing to next publication_number
********************
i: 719 / 37660 --- publication_number: US-11080259-B1
URL: https://patents.google.com/patent/US11080259B1
folder image_downloads/US-11080259-B1 already exists, continuing to next publication_number
********************
i: 720 / 37660 --- publication_number: US-11079303-B1
URL: https://patents.google.com/patent/US11079303B1
folder image_downloads/US-11079303-B1 already exists, continuing to next publication_number
********************
i: 721 / 37660 --- publication_number: US-11077564-B1
URL: https://patents.google.com/patent/US11077564B1
folder image_downloads/US-11077564-B1 already exists, continuing to next publication_number
********************
i: 722 / 37

folder image_downloads/US-10999132-B1 already exists, continuing to next publication_number
********************
i: 1491 / 37660 --- publication_number: US-10997426-B1
URL: https://patents.google.com/patent/US10997426B1
folder image_downloads/US-10997426-B1 already exists, continuing to next publication_number
********************
i: 1492 / 37660 --- publication_number: US-10999169-B1
URL: https://patents.google.com/patent/US10999169B1
folder image_downloads/US-10999169-B1 already exists, continuing to next publication_number
********************
i: 1493 / 37660 --- publication_number: US-10999407-B1
URL: https://patents.google.com/patent/US10999407B1
folder image_downloads/US-10999407-B1 already exists, continuing to next publication_number
********************
i: 1494 / 37660 --- publication_number: US-10997247-B1
URL: https://patents.google.com/patent/US10997247B1
folder image_downloads/US-10997247-B1 already exists, continuing to next publication_number
********************
i: 1495

folder image_downloads/EP-3237951-B1 already exists, continuing to next publication_number
********************
i: 2180 / 37660 --- publication_number: EP-3786085-A1
URL: https://patents.google.com/patent/EP3786085A1
folder image_downloads/EP-3786085-A1 already exists, continuing to next publication_number
********************
i: 2181 / 37660 --- publication_number: EP-2920684-B1
URL: https://patents.google.com/patent/EP2920684B1
folder image_downloads/EP-2920684-B1 already exists, continuing to next publication_number
********************
i: 2182 / 37660 --- publication_number: EP-3488426-B1
URL: https://patents.google.com/patent/EP3488426B1
folder image_downloads/EP-3488426-B1 already exists, continuing to next publication_number
********************
i: 2183 / 37660 --- publication_number: EP-3785444-A1
URL: https://patents.google.com/patent/EP3785444A1
folder image_downloads/EP-3785444-A1 already exists, continuing to next publication_number
********************
i: 2184 / 37660 --- 

folder image_downloads/US-10877669-B1 already exists, continuing to next publication_number
********************
i: 2898 / 37660 --- publication_number: US-10880585-B1
URL: https://patents.google.com/patent/US10880585B1
folder image_downloads/US-10880585-B1 already exists, continuing to next publication_number
********************
i: 2899 / 37660 --- publication_number: US-10880601-B1
URL: https://patents.google.com/patent/US10880601B1
folder image_downloads/US-10880601-B1 already exists, continuing to next publication_number
********************
i: 2900 / 37660 --- publication_number: CN-212246096-U
URL: https://patents.google.com/patent/CN212246096U
folder image_downloads/CN-212246096-U already exists, continuing to next publication_number
********************
i: 2901 / 37660 --- publication_number: CN-212244828-U
URL: https://patents.google.com/patent/CN212244828U
folder image_downloads/CN-212244828-U already exists, continuing to next publication_number
********************
i: 2902

...

downloading US10379894-20190813-D00001.png to image_downloads/US-10379894-B1/US10379894-20190813-D00001.png
downloading US10379894-20190813-D00002.png to image_downloads/US-10379894-B1/US10379894-20190813-D00002.png
downloading US10379894-20190813-D00003.png to image_downloads/US-10379894-B1/US10379894-20190813-D00003.png
downloading US10379894-20190813-D00004.png to image_downloads/US-10379894-B1/US10379894-20190813-D00004.png
downloading US10379894-20190813-D00005.png to image_downloads/US-10379894-B1/US10379894-20190813-D00005.png
downloading US10379894-20190813-D00006.png to image_downloads/US-10379894-B1/US10379894-20190813-D00006.png
downloading US10379894-20190813-D00007.png to image_downloads/US-10379894-B1/US10379894-20190813-D00007.png
downloading US10379894-20190813-D00008.png to image_downloads/US-10379894-B1/US10379894-20190813-D00008.png
https://patentimages.storage.googleapis.com/8b/1c/29/8b70b496494469/US10379894.pdf
downloading US10379894.pdf to image_downloads/US-1037

downloading US10379838-20190813-D00013.png to image_downloads/US-10379838-B1/US10379838-20190813-D00013.png
downloading US10379838-20190813-D00014.png to image_downloads/US-10379838-B1/US10379838-20190813-D00014.png
downloading US10379838-20190813-D00015.png to image_downloads/US-10379838-B1/US10379838-20190813-D00015.png
https://patentimages.storage.googleapis.com/08/11/6f/e982b6ff3fa56b/US10379838.pdf
downloading US10379838.pdf to image_downloads/US-10379838-B1/US10379838.pdf
********************
i: 8792 / 37660 --- publication_number: US-10382328-B1
URL: https://patents.google.com/patent/US10382328B1
making directory image_downloads/US-10382328-B1
found 13 images
found 1 PDFs
downloading US10382328-20190813-D00000.png to image_downloads/US-10382328-B1/US10382328-20190813-D00000.png
downloading US10382328-20190813-D00001.png to image_downloads/US-10382328-B1/US10382328-20190813-D00001.png
downloading US10382328-20190813-D00002.png to image_downloads/US-10382328-B1/US10382328-20190813

downloading US10382213-20190813-D00011.png to image_downloads/US-10382213-B1/US10382213-20190813-D00011.png
https://patentimages.storage.googleapis.com/92/12/d6/372c33f53ad5fb/US10382213.pdf
downloading US10382213.pdf to image_downloads/US-10382213-B1/US10382213.pdf
********************
i: 8797 / 37660 --- publication_number: US-10378902-B1
URL: https://patents.google.com/patent/US10378902B1
making directory image_downloads/US-10378902-B1
found 8 images
found 1 PDFs
downloading US10378902-20190813-D00000.png to image_downloads/US-10378902-B1/US10378902-20190813-D00000.png
downloading US10378902-20190813-D00001.png to image_downloads/US-10378902-B1/US10378902-20190813-D00001.png
downloading US10378902-20190813-D00002.png to image_downloads/US-10378902-B1/US10378902-20190813-D00002.png
downloading US10378902-20190813-D00003.png to image_downloads/US-10378902-B1/US10378902-20190813-D00003.png
downloading US10378902-20190813-D00004.png to image_downloads/US-10378902-B1/US10378902-20190813-

********************
i: 8803 / 37660 --- publication_number: US-D856323-S
URL: https://patents.google.com/patent/USD856323S1
making directory image_downloads/US-D856323-S
found 7 images
found 1 PDFs
downloading USD0856323-20190813-D00000.png to image_downloads/US-D856323-S/USD0856323-20190813-D00000.png
downloading USD0856323-20190813-D00001.png to image_downloads/US-D856323-S/USD0856323-20190813-D00001.png
downloading USD0856323-20190813-D00002.png to image_downloads/US-D856323-S/USD0856323-20190813-D00002.png
downloading USD0856323-20190813-D00003.png to image_downloads/US-D856323-S/USD0856323-20190813-D00003.png
downloading USD0856323-20190813-D00004.png to image_downloads/US-D856323-S/USD0856323-20190813-D00004.png
downloading USD0856323-20190813-D00005.png to image_downloads/US-D856323-S/USD0856323-20190813-D00005.png
downloading USD0856323-20190813-D00006.png to image_downloads/US-D856323-S/USD0856323-20190813-D00006.png
https://patentimages.storage.googleapis.com/c9/4e/e6/2e29a5

KeyboardInterrupt: 